# Analisis de vehiculos 

Se realiza el analisis de datos de vehiculos

Se importan las librerias que serán utilizadas

In [77]:
import pandas as pd
import plotly.express as px
import matplotlib.pyplot as plt
import numpy as np

Se necesita realizar un breve análisis exploratorio de datos (EDA) en Python para entender la estructura del archivo CSV, identificar los tipos de datos de las columnas, y detectar posibles valores faltantes o atípicos. Esto es fundamental antes de poder sugerir y crear la aplicación de visualización en Streamli

In [78]:
car_data = pd.read_csv('C:\\Users\\joser\\Documents\\tripleten\\GitHub\\proyecto_sprint7\\vehicles_us.csv') # leer los datos
print("--- Primeras 5 filas del DataFrame ---")
print(car_data.head())

print("\n--- Información del DataFrame (Tipos de datos y valores no nulos) ---")
print(car_data.info())

print("\n--- Conteo de valores faltantes por columna ---")
print(car_data.isnull().sum())

--- Primeras 5 filas del DataFrame ---
   price  model_year           model  condition  cylinders fuel  odometer  \
0   9400      2011.0          bmw x5       good        6.0  gas  145000.0   
1  25500         NaN      ford f-150       good        6.0  gas   88705.0   
2   5500      2013.0  hyundai sonata   like new        4.0  gas  110000.0   
3   1500      2003.0      ford f-150       fair        8.0  gas       NaN   
4  14900      2017.0    chrysler 200  excellent        4.0  gas   80903.0   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV         NaN     1.0  2018-06-23           19  
1    automatic  pickup       white     1.0  2018-10-19           50  
2    automatic   sedan         red     NaN  2019-02-07           79  
3    automatic  pickup         NaN     NaN  2019-03-22            9  
4    automatic   sedan       black     NaN  2019-04-02           28  

--- Información del DataFrame (Tipos de datos y valores no nulos) ---
<class 

Se realiza la limpieza de los datos

In [79]:
# 1. Tratar la columna `is_4wd` Los nulos representan la ausencia de 4WD, por lo que se rellenan con 0.0
car_data['is_4wd'] = car_data['is_4wd'].fillna(0.0).astype(int)

# 2. Tratar la columna `paint_color` Rellenar nulos con una categoría 'unknown'
car_data['paint_color'] = car_data['paint_color'].fillna('unknown')

# 3. Tratar `model_year` y `cylinders` Imputar nulos con la mediana del grupo 'model'
car_data['model_year'] = car_data.groupby('model')['model_year'].transform(lambda x: x.fillna(x.median()))
car_data['cylinders'] = car_data.groupby('model')['cylinders'].transform(lambda x: x.fillna(x.median()))

# 4. Tratar `odometer`. Imputar nulos con la mediana del grupo de 'model_year' y 'condition'
car_data['odometer'] = car_data.groupby(['model_year', 'condition'])['odometer'].transform(lambda x: x.fillna(x.median()))


Se convierten los datos a entero, se usa `.round()` antes de `.astype(int)` para asegurar que los valores flotantes imputados se conviertan correctamente, en el ciclo se usa 'Int64' si después de la imputación todavía hubiera NaNs. Dado que las columnas imputadas aún tienen el tipo flotante, se redondea

In [80]:
#  Conversión de Tipo 

# Convertir columnas a enteros (después de imputar los nulos en `model_year` y `cylinders`)
int_cols = ['price', 'model_year', 'cylinders', 'odometer']
for col in int_cols:
    car_data[col] = car_data[col].round(0).astype('Int64') # Int64 maneja valores NaN como nulos

# Mostrar el resultado después de la limpieza
print("\n--- Información del DataFrame Después de la Limpieza ---")
car_data.info()

print("\n--- Conteo de Valores Nulos Después de la Limpieza ---")
print(car_data.isnull().sum())

print("\n--- Primeras 5 Filas del DataFrame Después de la Limpieza ---")
print(car_data.head())


--- Información del DataFrame Después de la Limpieza ---
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   price         51525 non-null  Int64 
 1   model_year    51525 non-null  Int64 
 2   model         51525 non-null  object
 3   condition     51525 non-null  object
 4   cylinders     51525 non-null  Int64 
 5   fuel          51525 non-null  object
 6   odometer      51518 non-null  Int64 
 7   transmission  51525 non-null  object
 8   type          51525 non-null  object
 9   paint_color   51525 non-null  object
 10  is_4wd        51525 non-null  int64 
 11  date_posted   51525 non-null  object
 12  days_listed   51525 non-null  int64 
dtypes: Int64(4), int64(2), object(7)
memory usage: 5.3+ MB

--- Conteo de Valores Nulos Después de la Limpieza ---
price           0
model_year      0
model           0
condition       0
cylinders      

Se crea la columna 'Manufacturer' que sera usada en algunos graficos para mejor visualización

In [81]:
 # Crear la columna 'manufacturer' a partir de 'model' (primer palabra) 
car_data['manufacturer'] = car_data['model'].apply(lambda x: x.split(' ')[0].capitalize())
print("--- DataFrame con la Nueva Columna 'manufacturer' ---")
print(car_data[['model', 'manufacturer']].head(10))

--- DataFrame con la Nueva Columna 'manufacturer' ---
            model manufacturer
0          bmw x5          Bmw
1      ford f-150         Ford
2  hyundai sonata      Hyundai
3      ford f-150         Ford
4    chrysler 200     Chrysler
5    chrysler 300     Chrysler
6    toyota camry       Toyota
7     honda pilot        Honda
8     kia sorento          Kia
9     honda pilot        Honda


A continuación se generan los graficos de dispersión  a partir del millaje (odometro)

In [82]:

fig1 = px.histogram(
    car_data, x='odometer',
    title='Distribución de Millaje de Vehículos',
    labels={'odometer': 'Millaje (Millas)', 'count': 'Frecuencia'},
    ) # crear un histograma
fig1.show()


In [83]:
fig_scatter = px.scatter(
            car_data,
            x='odometer',
            y='price',
            color='condition',
            hover_data=['model', 'manufacturer'],
        title='Precio vs. Millaje por Condición',
        labels={'odometer': 'Millaje (Millas)', 'price': 'Precio ($)'}
    )
fig_scatter.show() # crear gráfico de dispersión

Se crean los graficos de conteo por tipo de vehiculo

In [84]:
# Gráfico de barras para el fabricante
type_grouped = car_data.groupby(['manufacturer', 'type']).size().reset_index(name='count')
fig = px.bar(
    type_grouped,
    x='manufacturer',
    y='count',
    color='type',
    title='Distribución de Tipos de Vehículo por Fabricante',
    labels={'manufacturer': 'Fabricante','count': 'Cantidad de Vehículos','type': 'Tipo de Vehículo'}
    )
fig.show()

In [85]:
 # Gráfico de barras para el tipo de vehículo
type_counts = car_data['type'].value_counts().reset_index()
type_counts.columns = ['Type', 'Count']
    
fig_type_count = px.bar(
    type_counts,
    x='Type',
    y='Count',
    orientation='v',
    color='Type',
    title='Número de Anuncios por Tipo de Vehículo',
    labels={'Count': 'Número de Vehículos', 'Type': 'Tipo de Vehículo'}
    )
fig_type_count.show()

Se crean los graficos por antiguedad

In [86]:
fig_year_bar = px.histogram(
        car_data,
        x='model_year',
        nbins=100,
        color = 'condition',
        title='Condición de Vehículos por Año del Modelo',
        labels={'model_year': 'Año del Modelo', 'condition': 'Condición'}
    )
fig_year_bar.show()

In [88]:
fig_year_hist = px.histogram(
        car_data,
        x='model_year',
        nbins=50,
        color='manufacturer',
        title='Distribución de Vehículos por Año del Modelo',
        labels={'model_year': 'Año del Modelo', 'count': 'Frecuencia'},
    
    )
fig_year_hist.show()